In [16]:
from libsvm.svmutil import *
import numpy as np

train_y, train_x = svm_read_problem('train1.txt')
test_y, test_x = svm_read_problem('test1.txt')

train_x = [list(train_x[i].values()) for i in range(len(train_x)) if train_y[i] in [11, 26]]
test_x = [list(test_x[i].values()) for i in range(len(test_x)) if test_y[i] in [11, 26]]
train_y = [1 if x == 11 else -1 if x == 26 else None for x in train_y if x in [11, 26]]
test_y = [1 if x == 11 else -1 if x == 26 else None for x in test_y if x in [11, 26]]


class DecisionStump:
    def __init__(self, dimension, threshold, direction):
        self.dimension = dimension
        self.threshold = threshold
        self.direction = direction

    def predict(self, X):
        return self.direction * np.sign(X[:, self.dimension] - self.threshold)

class AdaBoost:
    def __init__(self, n_estimators):
        self.n_estimators = n_estimators
        self.estimators = []
        self.alphas = []
        self.allerr = []

    def fit(self, X, y):
        n_samples = X.shape[0]
        weights = np.full(n_samples, 1 / n_samples)

        for _ in range(self.n_estimators):
            best_stump = self._find_best_stump(X, y, weights)
            error = self._compute_error(best_stump, X, y, weights)
            alpha = 0.5 * np.log((1 - error) / error)

            self.estimators.append(best_stump)
            self.alphas.append(alpha)

            predictions = best_stump.predict(X)
            #print(np.array(predictions==y).astype(int))
            weights *= np.exp(-alpha * y * predictions)
            weights /= np.sum(weights)

    def predict(self, X):
        predictions = np.zeros(X.shape[0])
        for stump, alpha in zip(self.estimators, self.alphas):
            predictions += alpha * stump.predict(X)
        return np.sign(predictions)

    def _find_best_stump(self, X, y, weights):
        n_samples, n_features = X.shape
        best_stump = None
        min_error = float('inf')
        #cnt=0
        for dimension in range(n_features):
            sorted_indices = np.argsort(X[:, dimension])
            #print(len(X[sorted_indices, dimension]))
            s_X = X[sorted_indices, dimension]
            #unique_values = np.unique(X[:, dimension])
            #print('u', s_X)
            thresholds = np.unique((s_X[:-1] + s_X[1:]) / 2)
            #print('aaa', thresholds)
            a = np.array(-100000000)
            thresholds = np.append(a,thresholds)
            #print(thresholds)
            for threshold in thresholds:
                for direction in [-1, 1]:
                    #cnt+=1
                    stump = DecisionStump(dimension, threshold, direction)
                    error = self._compute_error(stump, X, y, weights)
                    #self.allerr.append(error)
                    if error < min_error:
                        min_error = error
                        best_stump = stump
        #print(cnt)
        self.allerr.append(min_error)
        print(best_stump.dimension, best_stump.threshold,best_stump.direction)
        return best_stump

    def _compute_error(self, stump, X, y, weights):
        predictions = stump.predict(X)
        incorrect = predictions != y
        return np.sum(weights[incorrect])


In [ ]:

X = np.array(train_x)
y = np.array(train_y)

adaboost = AdaBoost(n_estimators=1000)
adaboost.fit(X, y)

test_X = np.array(test_x)
test_y = np.array(test_y)

print("min Ein(g): ",min(adaboost.allerr))
print("max Ein(g): ",max(adaboost.allerr))

pred_Ein_G = adaboost.predict(X)
print(np.mean(y != pred_Ein_G))

pred_Eout_G = adaboost.predict(test_X)
print(np.mean(test_y != pred_Eout_G))

# min Ein(g):  0.09018144975591785
# max Ein(g):  0.38191382316475186
# 0.0
# 0.002793296089385475


[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01  4.0000000e-01  4.6666700e-01
  5.3333350e-01  6.0000000e-01  6.6666650e-01  7.3333300e-01
  8.0000000e-01  8.6666700e-01  9.3333350e-01  1.0000000e+00]
[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.000

[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01  4.0000000e-01  4.6666700e-01
  5.3333350e-01  6.0000000e-01  6.6666650e-01  8.0000000e-01
  8.6666700e-01  9.3333350e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.00

[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01  4.0000000e-01  4.6666700e-01
  5.3333350e-01  6.0000000e-01  6.6666650e-01  7.3333300e-01
  8.0000000e-01  8.6666700e-01  9.3333350e-01  1.0000000e+00]
[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.333

[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01  5.3333350e-01  6.0000000e-01
  6.6666650e-01  7.3333300e-01  8.0000000e-01]
[-1.0000000e+08 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01
 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01
 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02  0.0000000e+00
  6.6666700e-02  1.3333335e-01  2.0000000e-01  2.6666650e-01
  3.3333300e-01  4.0000000e-01  4.6666700e-01  5.3333350e-01
  6.0000000e-01  6.6666650e-01  7.3333300e-01  8.0000000e-01]
11 0.0 1
[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-

[-1.0000000e+08 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01
 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01
 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02  0.0000000e+00
  6.6666700e-02  1.3333335e-01  2.0000000e-01  2.6666650e-01
  3.3333300e-01  4.0000000e-01  4.6666700e-01  5.3333350e-01
  6.6666650e-01]
[-1.0000000e+08 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01]
[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.

...

[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01  4.0000000e-01  4.6666700e-01
  5.3333350e-01  6.0000000e-01  6.6666650e-01  8.0000000e-01
  8.6666700e-01  9.3333350e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01]
[-1.0000000e+08 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01
 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01
 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02  0.0000000e+00
  6.6666700e-02  1.33

[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01  4.0000000e-01  4.6666700e-01
  5.3333350e-01  6.0000000e-01  6.6666650e-01  7.3333300e-01
  8.0000000e-01  8.6666700e-01  9.3333350e-01  1.0000000e+00]
[-1.0000000e+08 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01  5.3333350e-01  6.000

[-1.0000000e+08 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01
 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01
 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02  0.0000000e+00
  6.6666700e-02  1.3333335e-01  2.0000000e-01  2.6666650e-01
  3.3333300e-01  4.0000000e-01  4.6666700e-01  5.3333350e-01
  6.6666650e-01]
[-1.0000000e+08 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01]
[-1.0000000e+08 -8.6666700e-01 -8.0000000e-01 -7.3333300e-01
 -6.6666650e-01 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01
 -4.0000000e-01 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.

[-1.0000000e+08 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01
 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01
 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01
 -6.6666700e-02  0.0000000e+00  6.6666700e-02  1.3333335e-01
  2.0000000e-01  2.6666650e-01  3.3333300e-01  4.0000000e-01
  4.6666700e-01  5.3333350e-01  6.0000000e-01]
[-1.0000000e+08 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01  5.3333350e-01  6.0000000e-01
  6.6666650e-01  7.3333300e-01]
[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.6666650e-01
  3.3333300e-01]
[-1.0000000e+08 -4.6666700e-01 -4.0000000e-01 -3.3

[-1.0000000e+08 -1.0000000e+00 -9.3333350e-01 -8.6666700e-01
 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01 -6.0000000e-01
 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01 -3.3333300e-01
 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01 -6.6666700e-02
  0.0000000e+00  6.6666700e-02  1.3333335e-01  2.0000000e-01
  2.6666650e-01  3.3333300e-01  4.0000000e-01  4.6666700e-01
  5.3333350e-01  6.0000000e-01  6.6666650e-01  7.3333300e-01
  8.0000000e-01  8.6666700e-01  9.3333350e-01  1.0000000e+00]
[-1.0000000e+08 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01
 -1.3333335e-01 -6.6666700e-02  0.0000000e+00  6.6666700e-02
  1.3333335e-01  2.0000000e-01  2.6666650e-01  3.3333300e-01
  4.0000000e-01  4.6666700e-01  5.3333350e-01  6.0000000e-01]
[-1.0000000e+08 -8.0000000e-01 -7.3333300e-01 -6.6666650e-01
 -6.0000000e-01 -5.3333350e-01 -4.6666700e-01 -4.0000000e-01
 -3.3333300e-01 -2.6666650e-01 -2.0000000e-01 -1.3333335e-01
 -6.6666700e-02  0.0000000e+00  6.6666700e-02  1.3333335e-01
  2.0000000e-01  2.666